In [103]:
##IMPORT DEPENDENCIES##
#gym stuff#
import gym
from gym import Env
from gym.spaces import Discrete, Box, Dict, Tuple, MultiBinary, MultiDiscrete

#helpers#
import torch as th
import numpy as np
import random
import os
import torch.nn as nn

#stablebaselines#
from stable_baselines3 import PPO
from stable_baselines3.common.vec_env import DummyVecEnv
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.policies import ActorCriticPolicy


#data plitting#
from sklearn.model_selection import train_test_split

In [68]:
# Define a mapping of body parts to column ranges
body_parts_mapping = {
    'Head': (0, 1),
    'SpineShoulders': (3, 4),
    'SpineMid': (6, 7),
    'LeftShoulder': (9, 10),
    'RightShoulder': (12, 13),
    'LeftElbow': (15, 16),
    'RightElbow': (18, 19),
    'LeftWrist': (21, 22),
    'RightWrist': (24, 25),
    'SpineBase': (27, 28),
    'LeftHip': (30, 31),
    'RightHip': (33, 34),
    'LeftKnee': (36, 37),
    'RightKnee': (39, 40),
    'LeftAnkle': (42, 43),
    'RightAnkle': (45, 46),
}

In [69]:
data_folder = os.path.join('data_copy')

In [70]:
data_folder

'data_copy'

In [110]:
# Function to preprocess data
def preprocess_data(data_folder):
    joint_positions = []
    actions = []

    exercise_folders = os.listdir(data_folder)
    exercise_folders.remove('guide')
    exercise_folders.remove('plot') 

    # Define the output folder path
    output_folder = os.path.join("States and Actions")
    os.makedirs(output_folder, exist_ok=True)

    for exercise_folder in exercise_folders:

        exercise_path = os.path.join(data_folder, exercise_folder)
        exercise_path_list = os.listdir(exercise_path)
        
        for typedata_folder in exercise_path_list:
        
            typedata_path = os.path.join(exercise_path, typedata_folder)
            typedata_path_list = os.listdir(typedata_path)

            for typepatient_folder in typedata_path_list:

                typepatient_path = os.path.join(typedata_path, typepatient_folder)
                typepatient_path_list = os.listdir(typepatient_path)

                for patient_folder in typepatient_path_list:

                    patient_path = os.path.join(typepatient_path, patient_folder)
                    patient_path_list = os.listdir(patient_path)

                    for trial_file in patient_path_list:
                        if not trial_file.startswith('.'):  # Skip files/directories starting with a period
                            file_path = os.path.join(patient_path, trial_file)
                            joints_data = read_txt_file(file_path)
        
                            # Extract relevant columns based on body parts mapping
                            extracted_data = extract_body_parts(joints_data)
                            
                            # Print metadata
                            print('-----------------------------------------------')
                            print('TypePatient -', typepatient_folder)
                            print('Exercise -', exercise_folder)
                            print('Typedata -', typedata_folder)
                            print('Patient -', patient_folder)
                            print('Trial -', trial_file)
                            
                            # Process each instance and generate actions
                            instance_actions = generate_actions(extracted_data)
                            actions.extend(instance_actions)

                            # Save the joint positions
                            joint_positions_output_folder = os.path.join(output_folder, typepatient_folder, exercise_folder, typedata_folder, patient_folder)
                            os.makedirs(joint_positions_output_folder, exist_ok=True)
                            joint_positions_file = os.path.join(joint_positions_output_folder, f"{trial_file}_joint_positions.txt")
                            with open(joint_positions_file, 'w') as file:
                                for instance in extracted_data:
                                    file.write(f"Instance:\n")
                                    for joint, coords in instance.items():
                                        file.write(f"{joint}: {coords}\n")
                                    file.write("\n")
                            
                            # Save the actions as text file
                            actions_output_folder = os.path.join(output_folder, typepatient_folder, exercise_folder, typedata_folder, patient_folder)
                            os.makedirs(actions_output_folder, exist_ok=True)
                            actions_file = os.path.join(actions_output_folder, f"{trial_file}_actions.txt")
                            with open(actions_file, 'w') as file:
                                for action in instance_actions:
                                    file.write(f"{action[0]} {action[1]}\n")

                            joint_positions.append(extracted_data)
    
     # Split data into training and testing sets
    train_data, test_data = train_test_split(joint_positions, test_size=0.2, random_state=42)
    train_actions, test_actions = train_test_split( actions, test_size=0.2, random_state=42)
    
    print('The End')
    
    return train_data, test_data, train_actions, test_actions

# Function to read data from a text file
def read_txt_file(file_path):
    with open(file_path, 'r') as file:
        lines = file.readlines()
        joints_data = [list(map(float, line.split(';'))) for line in lines]
    return joints_data

# Function to extract relevant body parts from joint data
def extract_body_parts(joints_data):
    num_instances = len(joints_data)
    extracted_data = []

    # Iterate over instances
    for instance_idx in range(num_instances):
        instance_data = {}
        # Iterate over body parts
        for body_part, (start_col, end_col) in body_parts_mapping.items():
            body_part_data = joints_data[instance_idx][start_col:end_col + 1]
            instance_data[body_part] = body_part_data
        extracted_data.append(instance_data)

    return extracted_data

# Function to generate grid position from joint coordinates
def generate_grid(joint_coords):
    # Define grid size (adjust as needed)
    grid_size = (10, 10)
    # Determine grid position of the joint coordinates
    grid_x = int(joint_coords[0] * grid_size[0])
    grid_y = int(joint_coords[1] * grid_size[1])
    return grid_x, grid_y

# Function to generate actions based on joint positions
def generate_actions(extracted_data):
    actions = []
    instance_idx = 1  # Track instance number
    for i in range(0, len(extracted_data), 2):  # Generate actions for every other instance
        if i + 2 < len(extracted_data):
            # Extract wrist coordinates for current and next instances
            current_left_wrist = extracted_data[i]['LeftWrist']
            next_left_wrist = extracted_data[i + 2]['LeftWrist']
            current_right_wrist = extracted_data[i]['RightWrist']
            next_right_wrist = extracted_data[i + 2]['RightWrist']
            
            # Generate grid positions for wrist coordinates
            current_left_grid = generate_grid(current_left_wrist)
            next_left_grid = generate_grid(next_left_wrist)
            current_right_grid = generate_grid(current_right_wrist)
            next_right_grid = generate_grid(next_right_wrist)
            
            # Compare grid positions to determine movement direction for left wrist
            left_movement = compare_positions(current_left_grid, next_left_grid)
            # Compare grid positions to determine movement direction for right wrist
            right_movement = compare_positions(current_right_grid, next_right_grid)
            
            # Map grid position comparison to action
            left_action = f"{left_movement}" if left_movement != "Hold" else "Hold"
            right_action = f"{right_movement}" if right_movement != "Hold" else "Hold"
            
            # Print the action for the current instance range
            print(f"Action from instance {instance_idx} to {instance_idx+2}: Left-  {left_action}, Right-  {right_action}")
            
            actions.append((left_action, right_action))
            instance_idx += 2  # Move to the next instance
    return actions

# Function to compare grid positions and determine movement direction
def compare_positions(current_grid, next_grid):
    # Compare grid positions between current and next coordinates
    # Return movement direction based on the comparison result
    # Example implementation (adjust as needed)
    if current_grid[0] == next_grid[0] and current_grid[1] == next_grid[1]:
        return "Hold"
    elif current_grid[0] < next_grid[0]:
        if current_grid[1] < next_grid[1]:
            return "DownRight"
        elif current_grid[1] > next_grid[1]:
            return "UpRight"
        else:
            return "Right"
    elif current_grid[0] > next_grid[0]:
        if current_grid[1] < next_grid[1]:
            return "DownLeft"
        elif current_grid[1] > next_grid[1]:
            return "UpLeft"
        else:
            return "Left"
    else:
        if current_grid[1] < next_grid[1]:
            return "Down"
        elif current_grid[1] > next_grid[1]:
            return "Up"
    return "no movement detected"  # Default action if no movement detected

# Function to map left and right movement directions to action
def map_to_action(left_movement, right_movement):
    # Map left and right movement directions to action
    # Return the corresponding action
    return f"{left_movement}_{right_movement}"

In [ ]:
train_data, test_data, train_actions, test_actions = preprocess_data(data_folder)

    #Print the sizes of the train and test datasets
print("Size of train dataset:", len(train_data))
print("Size of test dataset:", len(test_data))

    # Print the sizes of the train and test datasets
print("Size of train actions dataset:", len(train_actions))
print("Size of test actions dataset:", len(test_actions))

-----------------------------------------------
TypePatient - affected
Exercise - E1
Typedata - capture
Patient - P01
Trial - E1_filt_captured_P01_affected_1.txt
Action from instance 1 to 3: Left-  Hold, Right-  Hold
Action from instance 3 to 5: Left-  Hold, Right-  Hold
Action from instance 5 to 7: Left-  Down, Right-  Hold
Action from instance 7 to 9: Left-  Right, Right-  Hold
Action from instance 9 to 11: Left-  Hold, Right-  Hold
Action from instance 11 to 13: Left-  Hold, Right-  Hold
Action from instance 13 to 15: Left-  Up, Right-  Hold
Action from instance 15 to 17: Left-  Left, Right-  Hold
Action from instance 17 to 19: Left-  Up, Right-  Hold
Action from instance 19 to 21: Left-  Hold, Right-  Hold
Action from instance 21 to 23: Left-  Up, Right-  Hold
Action from instance 23 to 25: Left-  Hold, Right-  Hold
Action from instance 25 to 27: Left-  Hold, Right-  Hold
Action from instance 27 to 29: Left-  Hold, Right-  Hold
-----------------------------------------------
TypePa

In [113]:
# TRAIN MODEL
log_path = os.path.join('Training', 'Logs')
model = PPO(CustomMlpPolicy, env, verbose=1, tensorboard_log=log_path)


model.learn(total_timesteps=50000)
#total_timesteps = 50000
#for timestep in range(total_timesteps):
    #obs = env.reset()
    #done = False
    #score = 0

    #while not done:
        #action = model.predict(obs)[0]  # Predict action using the model
        #obs, reward, done, info = env.step(action)
        #score += reward

    #print('Timestep:{} Score:{}'.format(timestep, score))
    # Optionally, log scores or other relevant information

    # Perform model training after each episode or a certain number of timesteps
    #model.learn(total_timesteps=1)  # Perform one training step


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Observation shape:  (3136,)


ValueError: could not broadcast input array from shape (3136,) into shape (98,)